In [ ]:
!wget https://huggingface.co/namkunerr/YOLOv1/resolve/main/datasets.zip

--2025-03-05 01:09:17--  https://huggingface.co/namkunerr/YOLOv1/resolve/main/datasets.zip
Resolving huggingface.co (huggingface.co)... 18.164.174.118, 18.164.174.17, 18.164.174.55, ...
Connecting to huggingface.co (huggingface.co)|18.164.174.118|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.hf.co/repos/cd/6f/cd6f6d2118aa17caf00f2fd78f5e23615a0603eb287389c0e1a6495aabd35bdd/d2a84346d69dd64abf0bd8626963e16d2ffbb83da4cb00c153b64f2525c01fe8?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27datasets.zip%3B+filename%3D%22datasets.zip%22%3B&response-content-type=application%2Fzip&Expires=1741140557&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTc0MTE0MDU1N319LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmhmLmNvL3JlcG9zL2NkLzZmL2NkNmY2ZDIxMThhYTE3Y2FmMDBmMmZkNzhmNWUyMzYxNWEwNjAzZWIyODczODljMGUxYTY0OTVhYWJkMzViZGQvZDJhODQzNDZkNjlkZDY0YWJmMGJkODYyNjk2M2UxNmQyZmZiYjgzZGE0Y2IwMGMxNTNiNjRmMjUy

In [ ]:
!unzip /content/datasets.zip >/dev/null 2>&1

In [ ]:
!wget https://huggingface.co/namkunerr/YOLOv1/resolve/main/noise.zip

--2025-03-05 01:09:26--  https://huggingface.co/namkunerr/YOLOv1/resolve/main/noise.zip
Resolving huggingface.co (huggingface.co)... 18.164.174.118, 18.164.174.17, 18.164.174.55, ...
Connecting to huggingface.co (huggingface.co)|18.164.174.118|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.hf.co/repos/cd/6f/cd6f6d2118aa17caf00f2fd78f5e23615a0603eb287389c0e1a6495aabd35bdd/d652ebd1caee91dd24fabf8ba22597682a5c6bdd105270bdcc5f0b1780b196e2?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27noise.zip%3B+filename%3D%22noise.zip%22%3B&response-content-type=application%2Fzip&Expires=1741140566&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTc0MTE0MDU2Nn19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmhmLmNvL3JlcG9zL2NkLzZmL2NkNmY2ZDIxMThhYTE3Y2FmMDBmMmZkNzhmNWUyMzYxNWEwNjAzZWIyODczODljMGUxYTY0OTVhYWJkMzViZGQvZDY1MmViZDFjYWVlOTFkZDI0ZmFiZjhiYTIyNTk3NjgyYTVjNmJkZDEwNTI3MGJkY2M1ZjBiMTc4MGIxOTZlM

In [ ]:
!unzip noise.zip >/dev/null 2>&1

In [ ]:
!pip install tensorflow_io

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 MB 12.6 MB/s eta 0:00:00


In [ ]:
import librosa
import numpy as np
import os
import glob
import soundfile as sf

sr = 8000  # Sample rate
segment_length = sr  # Độ dài mỗi đoạn 1 giây
output_dir = "data"  # Thư mục lưu đoạn âm thanh

# Load danh sách tệp
noisefiles = glob.glob('/content/noise/*.wav')  # Đường dẫn đến tệp nhiễu
files = glob.glob('/content/datasets/*.wav')  # Đường dẫn đến tệp sạch

def load_wav(filename, target_sr=8000):
    wav, _ = librosa.load(filename, sr=target_sr, mono=True)
    return wav

def repeat_and_crop_noise(noise, target_length):
    """
    Lặp lại đoạn nhiễu để có độ dài lớn hơn hoặc bằng đoạn âm thanh sạch.
    Sau đó cắt đoạn nhiễu có độ dài chính xác bằng đoạn âm thanh sạch.
    """
    if len(noise) < target_length:
        repeats = int(np.ceil(target_length / len(noise)))
        noise = np.tile(noise, repeats)[:target_length]
    else:
        noise = noise[:target_length]
    return noise

def add_white_noise(data, factor=0.03):
    noise = np.random.normal(0, factor * np.max(data), size=data.shape)
    return data + noise

def add_background_noise(clean_wav, noise_wav, factor=0.2):
    noise_wav = repeat_and_crop_noise(noise_wav, len(clean_wav))
    return clean_wav + factor * noise_wav

def split_audio_and_save(wav, clean_wav, segment_length, filename):
    assert len(wav) == len(clean_wav)
    num_segments = len(wav) // segment_length  # Số đoạn có thể lấy đủ 1 giây

    os.makedirs(f"{output_dir}/noise", exist_ok=True)
    os.makedirs(f"{output_dir}/clean", exist_ok=True)

    for i in range(num_segments):
        segment = wav[i * segment_length:(i + 1) * segment_length]
        clean_segment = clean_wav[i * segment_length:(i + 1) * segment_length]

        segment_path = os.path.join(output_dir, "noise", f"{os.path.basename(filename).replace('.wav', '')}_{i}.wav")
        clean_segment_path = os.path.join(output_dir, "clean", f"{os.path.basename(filename).replace('.wav', '')}_{i}.wav")

        sf.write(segment_path, segment, sr)
        sf.write(clean_segment_path, clean_segment, sr)

# Xử lý từng tệp
for filepath in files:
    clean_wav = load_wav(filepath)

    # Bỏ qua các tệp có thời lượng < 1 giây
    if len(clean_wav) < segment_length:
        print(f"Skipping {filepath} (duration < 1s)")
        continue

    noise_file = np.random.choice(noisefiles)
    noise_wav = load_wav(noise_file)

    # Thêm nhiễu trắng
    clean_noisy = add_white_noise(clean_wav)

    # Thêm nhiễu nền từ tệp
    mixed_noisy = add_background_noise(clean_noisy, noise_wav)

    # Cắt đoạn và lưu lại
    split_audio_and_save(mixed_noisy, clean_wav, segment_length, filepath)


Skipping /content/datasets/1643.wav (duration < 1s)
Skipping /content/datasets/225.wav (duration < 1s)
Skipping /content/datasets/258.wav (duration < 1s)
Skipping /content/datasets/780.wav (duration < 1s)
Skipping /content/datasets/211.wav (duration < 1s)
Skipping /content/datasets/1012.wav (duration < 1s)
Skipping /content/datasets/857.wav (duration < 1s)
Skipping /content/datasets/432.wav (duration < 1s)
Skipping /content/datasets/1653.wav (duration < 1s)
Skipping /content/datasets/675.wav (duration < 1s)
Skipping /content/datasets/381.wav (duration < 1s)
Skipping /content/datasets/592.wav (duration < 1s)
Skipping /content/datasets/384.wav (duration < 1s)
Skipping /content/datasets/1865.wav (duration < 1s)
Skipping /content/datasets/1135.wav (duration < 1s)
Skipping /content/datasets/1053.wav (duration < 1s)
Skipping /content/datasets/1396.wav (duration < 1s)
Skipping /content/datasets/856.wav (duration < 1s)
Skipping /content/datasets/453.wav (duration < 1s)
Skipping /content/datase

In [ ]:
def load_wav(filename, target_sr=8000):
    wav, sample_rate = librosa.load(filename, sr=target_sr, mono=True)
    print("sample_rate",sample_rate)
    return wav
audio = load_wav("/content/data/noise/1000_0.wav")
print(audio)
print(len(audio))


sample_rate 8000
[-0.01608276  0.00488281  0.00204468 ...  0.05267334  0.02307129
  0.01815796]
8000


In [ ]:
import tensorflow as tf
frame_length=510
n_fft=  510
frame_step =240
x =tf.signal.stft(audio, frame_length=frame_length, fft_length=n_fft,
                                      frame_step=frame_step)
print(x)
print(x.shape)

tf.Tensor(
[[ 0.06666115+0.j         -0.15689431-0.0102934j   0.18672001-0.06829412j
  ... -0.02755237-0.04811129j  0.1479059 +0.03172308j
  -0.23775461+0.j        ]
 [-0.19519901+0.j          0.14737542+0.07247853j  0.0364016 -0.06163898j
  ...  0.01376472+0.01930471j  0.02348254-0.0440127j
  -0.09984013-0.j        ]
 [ 0.08036925+0.j         -0.15201679-0.06602606j  0.12131865+0.08588222j
  ... -0.11537276+0.08406717j  0.04900991-0.12211196j
   0.00988808+0.j        ]
 ...
 [-0.10190891+0.j          0.1342032 -0.01453425j -0.16149852+0.08643234j
  ... -0.1616418 +0.13006772j  0.08510008-0.07861984j
  -0.07028058-0.j        ]
 [ 0.00205904+0.j          0.00250055-0.06652473j -0.05096461+0.11375362j
  ...  0.00574557+0.05142624j -0.00943812-0.02236502j
   0.07080991-0.j        ]
 [ 0.2186966 +0.j         -0.17624018+0.01291914j  0.08225442-0.00125404j
  ...  0.0963833 +0.07755457j -0.19654521-0.02230175j
   0.23885483-0.j        ]], shape=(32, 256), dtype=complex64)
(32, 256)


In [ ]:
stft_result = librosa.stft(audio, n_fft=510, hop_length=240,center= False)
print(stft_result.T)
print(stft_result.T.shape)

[[ 0.06666113+0.j         -0.15689431-0.01029342j  0.18672004-0.06829415j
  ... -0.02755236-0.04811129j  0.14790589+0.03172309j
  -0.23775461+0.j        ]
 [-0.19519901+0.j          0.14737545+0.07247852j  0.0364016 -0.06163896j
  ...  0.01376473+0.01930469j  0.02348254-0.04401269j
  -0.09984013+0.j        ]
 [ 0.08036922+0.j         -0.15201676-0.06602608j  0.12131863+0.08588219j
  ... -0.11537277+0.08406714j  0.04900991-0.12211196j
   0.00988811+0.j        ]
 ...
 [-0.10190893+0.j          0.13420331-0.01453435j -0.16149849+0.08643226j
  ... -0.16164169+0.1300676j   0.08510005-0.07861976j
  -0.07028057+0.j        ]
 [ 0.00205897+0.j          0.00250058-0.06652482j -0.05096477+0.11375352j
  ...  0.00574558+0.05142618j -0.00943811-0.02236487j
   0.07080979+0.j        ]
 [ 0.21869668+0.j         -0.1762405 +0.01291926j  0.08225437-0.00125402j
  ...  0.09638325+0.07755458j -0.19654514-0.02230199j
   0.23885483+0.j        ]]
(32, 256)


In [ ]:
data =np.array([1,2,2,1,3,4,5,1],np.float32)
stft_result = librosa.stft(data, n_fft=4, hop_length=2,center= False)
print(stft_result)
print(stft_result.shape)

[[ 3.5+0.j   5.5+0.j   7.5+0.j ]
 [-2. -0.5j -3. +1.5j -5. -1.5j]
 [ 0.5+0.j   0.5+0.j   2.5+0.j ]]
(3, 3)


In [ ]:
from IPython.display import Audio
import librosa
y,sr = librosa.load("/content/data/clean/1000_0.wav",sr = 8000)
print("sr",sr)
print("len(y)",len(y))
Audio("/content/data/clean/1000_0.wav")

sr 8000
len(y) 8000


In [ ]:
from IPython.display import Audio
import librosa
y,sr = librosa.load("/content/data/noise/1000_0.wav",sr = 8000)
print("sr",sr)
print("len(y)",len(y))
Audio("/content/data/noise/1000_0.wav")

sr 8000
len(y) 8000


In [ ]:
import tensorflow as tf

class NoiseDataset(tf.data.Dataset):
    def __new__(cls, noisy_files, clean_files,
                sr=8000,
                frame_length=510,
                n_fft=510,
                frame_step=240,
                batch_size=64):
        """
        noisy_files: Danh sách đường dẫn đến file âm thanh có nhiễu
        clean_files: Danh sách đường dẫn đến file âm thanh sạch
        sr: Sample rate
        n_fft: Số điểm FFT cho STFT
        frame_length: Độ dài frame khi thực hiện STFT
        frame_step: Bước nhảy khi thực hiện STFT
        batch_size: Kích thước batch khi load dữ liệu
        """
        assert len(clean_files) == len(noisy_files), "Số lượng file sạch và nhiễu phải bằng nhau!"

        dataset = tf.data.Dataset.from_tensor_slices((clean_files, noisy_files))

        def process_audio(clean_path, noisy_path):
            """ Load file audio bằng TensorFlow, tính STFT """
            wav_clean = cls.load_wav(clean_path, sr)
            wav_noisy = cls.load_wav(noisy_path, sr)

            spectrogram_noisy, spectrogram_clean = cls.convert_to_spectrogram(wav_noisy, wav_clean, n_fft, frame_length, frame_step)

            spectrogram_noisy = cls.split_real_imag(spectrogram_noisy)
            spectrogram_clean = cls.split_real_imag(spectrogram_clean)

            return spectrogram_noisy, spectrogram_clean

        dataset = dataset.map(process_audio, num_parallel_calls=tf.data.AUTOTUNE)
        dataset = dataset.batch(batch_size).prefetch(tf.data.AUTOTUNE)
        return dataset

    @staticmethod
    def load_wav(filename, target_sr=8000):
        """ Load file âm thanh bằng TensorFlow """
        file_content = tf.io.read_file(filename)
        wav, sr = tf.audio.decode_wav(file_content, desired_channels=1)
        wav = tf.squeeze(wav, axis=-1)  # Chuyển từ (samples, 1) -> (samples,)


        return wav

    @staticmethod
    def convert_to_spectrogram(wav_noisy, wav_clean, n_fft, frame_length, frame_step):
        """ Tính toán STFT của tín hiệu """
        spectrogram_noisy = tf.signal.stft(wav_noisy, frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)
        spectrogram_clean = tf.signal.stft(wav_clean, frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)
        return spectrogram_noisy, spectrogram_clean

    @staticmethod
    def split_real_imag(spectrogram):
        """ Tách phần thực và ảo của phổ """
        real_part = tf.math.real(spectrogram)
        imag_part = tf.math.imag(spectrogram)
        stacked = tf.stack([real_part, imag_part], axis=-1)  # (time, freq, 2)
        return stacked


In [ ]:
from sklearn.model_selection import train_test_split
import glob
noise_files = glob.glob('/content/data/noise/*.wav')
clean_files = [i.replace("noise","clean") for i in noise_files]
assert len(clean_files) == len(noise_files)
noisy_train, noisy_test, clean_train, clean_test = train_test_split(
    noise_files, clean_files, test_size=0.1, random_state=42
)

print("Train set:")
print(noisy_train)
print(clean_train)

print("\nTest set:")
print(noisy_test)
print(clean_test)

Train set:
['/content/data/noise/1532_9.wav', '/content/data/noise/738_0.wav', '/content/data/noise/779_0.wav', '/content/data/noise/1817_1.wav', '/content/data/noise/1603_5.wav', '/content/data/noise/1494_2.wav', '/content/data/noise/1851_2.wav', '/content/data/noise/56_0.wav', '/content/data/noise/667_3.wav', '/content/data/noise/1408_0.wav', '/content/data/noise/983_6.wav', '/content/data/noise/1809_3.wav', '/content/data/noise/1326_6.wav', '/content/data/noise/428_0.wav', '/content/data/noise/1049_0.wav', '/content/data/noise/1210_3.wav', '/content/data/noise/1843_0.wav', '/content/data/noise/645_1.wav', '/content/data/noise/1772_0.wav', '/content/data/noise/472_4.wav', '/content/data/noise/1886_3.wav', '/content/data/noise/1108_2.wav', '/content/data/noise/1611_2.wav', '/content/data/noise/1795_2.wav', '/content/data/noise/15_4.wav', '/content/data/noise/510_1.wav', '/content/data/noise/1287_3.wav', '/content/data/noise/732_1.wav', '/content/data/noise/628_1.wav', '/content/data/n

In [ ]:
train_dataset = NoiseDataset(noisy_train, clean_train)
test_dataset = NoiseDataset(noisy_test, clean_test)


In [ ]:
for x, y in train_dataset.take(1):
    print(f"Feature shape: {x.shape}, Label shape: {y.shape}")


Feature shape: (64, 32, 256, 2), Label shape: (64, 32, 256, 2)


In [ ]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import (
    BatchNormalization,
    Conv2D,
    Conv2DTranspose,
    MaxPooling2D,
    Input,
    concatenate,
    multiply,
    add,
    Activation,
    LeakyReLU
)
from tensorflow import keras
from tensorflow.keras import layers

# Định nghĩa Attention Gate và Attention Concatenation
def attention_gate(inp_1, inp_2, n_intermediate_filters):
    """
    Attention gate: nén cả 2 đầu vào xuống n_intermediate_filters, sau đó tính attention map.
    Áp dụng theo đề xuất của Oktay et al. trong Attention U-Net.
    """
    inp_1_conv = Conv2D(
        n_intermediate_filters,
        kernel_size=1,
        strides=1,
        padding="same",
        kernel_initializer="he_normal"
    )(inp_1)
    inp_2_conv = Conv2D(
        n_intermediate_filters,
        kernel_size=1,
        strides=1,
        padding="same",
        kernel_initializer="he_normal"
    )(inp_2)

    f = Activation("relu")(add([inp_1_conv, inp_2_conv]))
    g = Conv2D(
        filters=1,
        kernel_size=1,
        strides=1,
        padding="same",
        kernel_initializer="he_normal"
    )(f)
    h = Activation("sigmoid")(g)
    return multiply([inp_1, h])

def attention_concat(conv_below, skip_connection):
    """
    Kết hợp đầu ra của tầng upsampling (conv_below) với skip connection đã được xử lý qua attention gate.
    """
    below_filters = conv_below.shape[-1]  # Sử dụng thuộc tính .shape thay vì get_shape()
    attention_across = attention_gate(skip_connection, conv_below, below_filters)
    return concatenate([conv_below, attention_across])

# Model U-Net 3 blocks với Attention Gate ở phần Decoder
def unet_3blocks_with_attention(input_size=(2, 32, 256), num_classes=2):
    inputs = layers.Input(shape=input_size)

    ### Encoder Block 1
    c1 = Conv2D(16, (3, 3), padding='same')(inputs)
    c1 = BatchNormalization()(c1)
    c1 = LeakyReLU(alpha=0.2)(c1)
    c1 = Conv2D(16, (3, 3), padding='same')(c1)
    c1 = BatchNormalization()(c1)
    c1 = LeakyReLU(alpha=0.2)(c1)
    p1 = MaxPooling2D(pool_size=(2, 2))(c1)  # (256,32) -> (128,16)

    ### Encoder Block 2
    c2 = Conv2D(32, (3, 3), padding='same')(p1)
    c2 = BatchNormalization()(c2)
    c2 = LeakyReLU(alpha=0.2)(c2)
    c2 = Conv2D(32, (3, 3), padding='same')(c2)
    c2 = BatchNormalization()(c2)
    c2 = LeakyReLU(alpha=0.2)(c2)
    p2 = MaxPooling2D(pool_size=(2, 2))(c2)  # (128,16) -> (64,8)

    ### Encoder Block 3
    c3 = Conv2D(64, (3, 3), padding='same')(p2)
    c3 = BatchNormalization()(c3)
    c3 = LeakyReLU(alpha=0.2)(c3)
    c3 = Conv2D(64, (3, 3), padding='same')(c3)
    c3 = BatchNormalization()(c3)
    c3 = LeakyReLU(alpha=0.2)(c3)
    p3 = MaxPooling2D(pool_size=(2, 2))(c3)  # (64,8) -> (32,4)

    ### Bottleneck
    b = Conv2D(128, (3, 3), padding='same')(p3)
    b = BatchNormalization()(b)
    b = LeakyReLU(alpha=0.2)(b)
    b = Conv2D(128, (3, 3), padding='same')(b)
    b = BatchNormalization()(b)
    b = LeakyReLU(alpha=0.2)(b)

    ### Decoder Block 1
    u1 = Conv2DTranspose(64, (3, 3), strides=(2, 2), padding='same')(b)  # (32,4)->(64,8)
    u1 = attention_concat(conv_below=u1, skip_connection=c3)
    u1 = BatchNormalization()(u1)
    u1 = LeakyReLU(alpha=0.2)(u1)
    u1 = Conv2D(64, (3, 3), padding='same')(u1)
    u1 = BatchNormalization()(u1)
    u1 = LeakyReLU(alpha=0.2)(u1)

    ### Decoder Block 2
    u2 = Conv2DTranspose(32, (3, 3), strides=(2, 2), padding='same')(u1)  # (64,8)->(128,16)
    u2 = attention_concat(conv_below=u2, skip_connection=c2)
    u2 = BatchNormalization()(u2)
    u2 = LeakyReLU(alpha=0.2)(u2)
    u2 = Conv2D(32, (3, 3), padding='same')(u2)
    u2 = BatchNormalization()(u2)
    u2 = LeakyReLU(alpha=0.2)(u2)

    ### Decoder Block 3
    u3 = Conv2DTranspose(16, (3, 3), strides=(2, 2), padding='same')(u2)  # (128,16)->(256,32)
    u3 = attention_concat(conv_below=u3, skip_connection=c1)
    u3 = BatchNormalization()(u3)
    u3 = LeakyReLU(alpha=0.2)(u3)
    u3 = Conv2D(16, (3, 3), padding='same')(u3)
    u3 = BatchNormalization()(u3)
    u3 = LeakyReLU(alpha=0.2)(u3)

    ### Output layer: chuyển số kênh về num_classes
    outputs = Conv2D(num_classes, (1, 1))(u3)

    model = Model(inputs=inputs, outputs=outputs)
    return model

model = unet_3blocks_with_attention(input_size=( 32, 256,2), num_classes=2)
model.summary()

/usr/local/lib/python3.11/dist-packages/keras/src/layers/activations/leaky_relu.py:41: UserWarning: Argument `alpha` is deprecated. Use `negative_slope` instead.
  warnings.warn(


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)              ┃ Output Shape           ┃        Param # ┃ Connected to           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)  │ (None, 32, 256, 2)     │              0 │ -                      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d (Conv2D)           │ (None, 32, 256, 16)    │            304 │ input_layer[0][0]      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization       │ (None, 32, 256, 16)    │             64 │ conv2d[0][0]           │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ leaky_re_lu (LeakyReLU)   │ (None, 32, 256, 16)    │              0 │ batch_normalization[0… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_1 (Conv2D)         │ (None, 32, 256, 16)    │          2,320 │ leaky_re_lu[0][0]      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_1     │ (None, 32, 256, 16)    │             64 │ conv2d_1[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ leaky_re_lu_1 (LeakyReLU) │ (None, 32, 256, 16)    │              0 │ batch_normalization_1… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ max_pooling2d             │ (None, 16, 128, 16)    │              0 │ leaky_re_lu_1[0][0]    │
│ (MaxPooling2D)            │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_2 (Conv2D)         │ (None, 16, 128, 32)    │          4,640 │ max_pooling2d[0][0]    │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_2     │ (None, 16, 128, 32)    │            128 │ conv2d_2[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ leaky_re_lu_2 (LeakyReLU) │ (None, 16, 128, 32)    │              0 │ batch_normalization_2… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_3 (Conv2D)         │ (None, 16, 128, 32)    │          9,248 │ leaky_re_lu_2[0][0]    │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_3     │ (None, 16, 128, 32)    │            128 │ conv2d_3[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ leaky_re_lu_3 (LeakyReLU) │ (None, 16, 128, 32)    │              0 │ batch_normalization_3… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ max_pooling2d_1           │ (None, 8, 64, 32)      │              0 │ leaky_re_lu_3[0][0]    │
│ (MaxPooling2D)            │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_4 (Conv2D)         │ (None, 8, 64, 64)      │         18,496 │ max_pooling2d_1[0][0]  │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_4

 Total params: 501,525 (1.91 MB)

 Trainable params: 499,893 (1.91 MB)

 Non-trainable params: 1,632 (6.38 KB)

In [ ]:
from tensorflow.keras.utils import plot_model
plot_model(model, show_shapes=True)

In [ ]:
from tensorflow.keras import layers, models, callbacks
import tensorflow as tf

# Khởi tạo mô hình UNet với input shape và số class
model = unet_3blocks_with_attention(input_size=(32, 256, 2), num_classes=2)

# Loss function và Optimizer với gradient clipping
optimizer = tf.keras.optimizers.Adam(learning_rate=0.001, clipnorm=1.0)
loss_fn = tf.keras.losses.Huber()

model.compile(optimizer=optimizer, loss=loss_fn)

# Callback để lưu trọng số sau mỗi epoch
checkpoint_callback = callbacks.ModelCheckpoint(
    filepath="checkpoints/model_epoch_{epoch:02d}.weights.h5",
    save_weights_only=True,
    save_best_only=True,  # Chỉ lưu mô hình tốt nhất
    monitor="val_loss",   # Theo dõi validation loss thay vì train loss
    verbose=1
)

# Các callbacks bổ sung
early_stopping = callbacks.EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
reduce_lr = callbacks.ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=2, min_lr=1e-6)

model.fit(
    train_dataset,
    validation_data=test_dataset,  # Thêm tập test để đánh giá
    epochs=50,
    callbacks=[early_stopping, reduce_lr, checkpoint_callback]
)

/usr/local/lib/python3.11/dist-packages/keras/src/layers/activations/leaky_relu.py:41: UserWarning: Argument `alpha` is deprecated. Use `negative_slope` instead.
  warnings.warn(


Epoch 1/50
91/91 ━━━━━━━━━━━━━━━━━━━━ 0s 303ms/step - loss: 0.1288
Epoch 1: val_loss improved from inf to 0.04845, saving model to checkpoints/model_epoch_01.weights.h5
91/91 ━━━━━━━━━━━━━━━━━━━━ 71s 361ms/step - loss: 0.1283 - val_loss: 0.0485 - learning_rate: 0.0010
Epoch 2/50
90/91 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step - loss: 0.0321
Epoch 2: val_loss improved from 0.04845 to 0.04174, saving model to checkpoints/model_epoch_02.weights.h5
91/91 ━━━━━━━━━━━━━━━━━━━━ 35s 88ms/step - loss: 0.0320 - val_loss: 0.0417 - learning_rate: 0.0010
Epoch 3/50
90/91 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step - loss: 0.0257
Epoch 3: val_loss improved from 0.04174 to 0.03410, saving model to checkpoints/model_epoch_03.weights.h5
91/91 ━━━━━━━━━━━━━━━━━━━━ 11s 91ms/step - loss: 0.0257 - val_loss: 0.0341 - learning_rate: 0.0010
Epoch 4/50
90/91 ━━━━━━━━━━━━━━━━━━━━ 0s 78ms/step - loss: 0.0230
Epoch 4: val_loss improved from 0.03410 to 0.02955, saving model to checkpoints/model_epoch_04.weights.h5
91/91 ━━━━━━━━━━━

In [ ]:
!pip install sounddevice

In [ ]:
import tensorflow as tf
import numpy as np

import librosa

import IPython.display as ipd

def play_audio(audio, sr=8000):
    """Phát lại âm thanh trong Jupyter Notebook"""
    return ipd.Audio(audio, rate=sr)

def denoise_audio(file_path, sr=8000, frame_length=510, n_fft=510, frame_step=240):
    """
    Load một file âm thanh nhiễu, xử lý qua model và phát lại âm thanh đã khử nhiễu.

    model: Mô hình khử nhiễu (nhận đầu vào là spectrogram và trả về spectrogram sạch)
    file_path: Đường dẫn đến file âm thanh nhiễu
    sr: Sample rate
    n_fft: Số điểm FFT
    frame_length: Độ dài khung STFT
    frame_step: Bước nhảy STFT
    """
    # 1. Load tệp âm thanh
    wav_noisy = NoiseDataset.load_wav(file_path, sr)

    # 2. Chuyển đổi thành phổ STFT
    spectrogram_noisy = tf.signal.stft(wav_noisy, frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)
    spectrogram_noisy = NoiseDataset.split_real_imag(spectrogram_noisy)
    spectrogram_noisy = tf.expand_dims(spectrogram_noisy, axis=0)  # Thêm batch dimension

    # 3. Dự đoán với model
    model = unet_3blocks_with_attention(input_size=(32, 256, 2), num_classes=2)
    model.load_weights("/content/checkpoints/model_epoch_36.weights.h5")
    spectrogram_clean = model(spectrogram_noisy, training=False)

    # 4. Chuyển spectrogram thành tín hiệu âm thanh
    spectrogram_clean = tf.complex(spectrogram_clean[..., 0], spectrogram_clean[..., 1])
    wav_clean = tf.signal.inverse_stft(spectrogram_clean[0], frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)

    # 5. Chuẩn hóa giá trị về [-1, 1]
    wav_clean = wav_clean / tf.reduce_max(tf.abs(wav_clean))

    # 6. Phát lại âm thanh
    wav_clean_np = wav_clean.numpy()
    wav_clean_np = np.squeeze(wav_clean_np)  # Loại bỏ batch dimension
    print(len(wav_clean_np))
    sf.write("clean_audio.wav", wav_clean_np,samplerate=8000)
    return wav_clean_np

In [ ]:
denoise_audio(file_path="/content/data/noise/1001_0.wav")

7950


array([ 0.0000000e+00, -4.0897706e-07,  5.7088471e-07, ...,
       -1.0896989e-06, -5.4084666e-07,  4.0388372e-08], dtype=float32)

In [ ]:
from IPython.display import Audio
import librosa

Audio("/content/clean_audio.wav")


In [ ]:
Audio("custom_noise.wav")

In [ ]:
def split_and_eval(audio_path):
  audio, _ = librosa.load(audio_path, sr=8000)

  max_len = len(audio)//8000
  all_audio = []
  for i in range(max_len):
    start = i*8000
    end = (i+1)*8000
    tmp_audio = audio[start:end]

    spectrogram_noisy = tf.signal.stft(tmp_audio, frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)
    spectrogram_noisy = NoiseDataset.split_real_imag(spectrogram_noisy)
    spectrogram_noisy = tf.expand_dims(spectrogram_noisy, axis=0)  # Thêm batch dimension

    # 3. Dự đoán với model
    model = unet_3blocks_with_attention(input_size=(32, 256, 2), num_classes=2)
    model.load_weights("/content/checkpoints/model_epoch_36.weights.h5")
    spectrogram_clean = model(spectrogram_noisy, training=False)

    # 4. Chuyển spectrogram thành tín hiệu âm thanh
    spectrogram_clean = tf.complex(spectrogram_clean[..., 0], spectrogram_clean[..., 1])
    wav_clean = tf.signal.inverse_stft(spectrogram_clean[0], frame_length=frame_length, frame_step=frame_step, fft_length=n_fft)

    # 5. Chuẩn hóa giá trị về [-1, 1]
    wav_clean = wav_clean / tf.reduce_max(tf.abs(wav_clean))

    # 6. Phát lại âm thanh
    wav_clean_np = wav_clean.numpy()
    wav_clean_np = np.squeeze(wav_clean_np)  # Loại bỏ batch dimension

    all_audio.append(wav_clean_np)

  res_audio = np.concatenate(all_audio)
  print(len(res_audio))
  sf.write("clean_audio.wav", res_audio,samplerate=8000)




In [ ]:
def mix_audio(clean_file, noise_file, factor=0.2):
    clean_wav = librosa.load(clean_file, sr=8000)[0]
    noise_wav = librosa.load(noise_file, sr=8000)[0]
    noise_wav = repeat_and_crop_noise(noise_wav, len(clean_wav))
    clean_wav = clean_wav.astype(np.float32)
    noise_wav = noise_wav.astype(np.float32)

    res = clean_wav + factor * noise_wav
    sf.write("custom_noise.wav",res,samplerate=8000)
mix_audio("/content/ShortCuts-20241229-Earth (mp3cut.net).mp3","/content/mixkit-small-crowd-clapping-3035.wav")

In [ ]:
split_and_eval("custom_noise.wav")

/usr/local/lib/python3.11/dist-packages/keras/src/layers/activations/leaky_relu.py:41: UserWarning: Argument `alpha` is deprecated. Use `negative_slope` instead.
  warnings.warn(


763200


In [ ]:
# Convert Keras model to a tflite model
converter = tf.lite.TFLiteConverter.from_keras_model(model)
converter.optimizations = [tf.lite.Optimize.OPTIMIZE_FOR_SIZE]
tflite_model = converter.convert()
tflite_model_name = 'denoi'
open(tflite_model_name + '.tflite', 'wb').write(tflite_model)

Saved artifact at '/tmp/tmpffzqaa0h'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): TensorSpec(shape=(None, 32, 256, 2), dtype=tf.float32, name='keras_tensor_71')
Output Type:
  TensorSpec(shape=(None, 32, 256, 2), dtype=tf.float32, name=None)
Captures:
  133746074230736: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133746074231312: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647759696: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647762000: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647762768: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647763920: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647765456: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647765648: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744647765840: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133744933012688: TensorSpec(shape=(), dtype=tf.resource, name=None)
  133

538776

In [ ]:
def hex_to_c_array(hex_data, var_name):

  c_str = ''

  # Create header guard
  c_str += '#ifndef ' + var_name.upper() + '_H\n'
  c_str += '#define ' + var_name.upper() + '_H\n\n'

  # Add array length at top of file
  c_str += '\nunsigned int ' + var_name + '_len = ' + str(len(hex_data)) + ';\n'

  # Declare C variable
  c_str += 'unsigned char ' + var_name + '[] = {'
  hex_array = []
  for i, val in enumerate(hex_data) :

    # Construct string from hex
    hex_str = format(val, '#04x')

    # Add formatting so each line stays within 80 characters
    if (i + 1) < len(hex_data):
      hex_str += ','
    if (i + 1) % 12 == 0:
      hex_str += '\n '
    hex_array.append(hex_str)

  # Add closing brace
  c_str += '\n ' + format(' '.join(hex_array)) + '\n};\n\n'

  # Close out header guard
  c_str += '#endif //' + var_name.upper() + '_H'

  return c_str

In [ ]:
# Write TFLite model to a C source (or header) file
c_model_name ="denoi"
with open(c_model_name + '.h', 'w') as file:
  file.write(hex_to_c_array(tflite_model, c_model_name))